In [15]:
import shapely
import geopandas as gpd
import pandas as pd
import numpy as np


## Input
This is the only place where you have to change code if you want to change the dates or concentrations that you are filtering out, or if the column names of your files are different.

In [16]:
data_file_name = '../CENTRALVALLEY_NO3N.csv'


year_range = [90,10] # Only put the last two numbers of the year (e.g. 1990 > 90) Date format is "MM/DD/YY"
date_column_name = 'GM_SAMP_COLLECTION_DATE'

concentration_treshold = 0
concentration_column_name = 'GM_RESULT'

lat_column_name = 'GM_LATITUDE'
lon_column_name = 'GM_LONGITUDE'



# whenever want to add extra columns
keep_columns=[date_column_name, concentration_column_name, 'GM_WELL_CATEGORY']


---

### Load all zipcode polygons:

In [17]:
zip_gdf = gpd.read_file("census_zipcode/central_valley_zip.shp")[['Zipcode','geometry']]
zip_gdf.head()

Zipcode                                           geometry
0   94514  POLYGON ((-137798.626 -21072.462, -137753.179 ...
1   95669  POLYGON ((-87179.121 56293.050, -87172.122 562...
2   95901  MULTIPOLYGON (((-124077.016 149359.370, -12404...
3   95974  POLYGON ((-160902.018 163396.734, -160934.773 ...
4   95979  POLYGON ((-229918.232 136775.281, -229954.603 ...

In [18]:
shapely.ops.unary_union(zip_gdf['geometry'].values)

In [19]:
print(len(zip_gdf))

372


### Load and filter main data:
Here we are filtering by date, and by concentration

In [20]:
# Load full file:
df = pd.read_csv(data_file_name)

# Delete columns we don't need: 
df = df[[lat_column_name, lon_column_name]+ keep_columns]

# Filter rows by date:
dates_bool = pd.Series([(int(df[date_column_name][i][-2:]) >= year_range[0]) |
                        (int(df[date_column_name][i][-2:]) <= year_range[1])
                        for i in range(len(df))])
df = df[dates_bool]
df = df.reset_index().drop('index', axis=1)

# Filter rows by concentration:
conc_bool = pd.Series([df[concentration_column_name][i] >= concentration_treshold
                        for i in range(len(df))])
df = df[conc_bool]
df = df.reset_index().drop('index', axis=1)

df.head()
print(df)

        GM_LATITUDE  GM_LONGITUDE GM_SAMP_COLLECTION_DATE  GM_RESULT  \
0         38.759847   -122.615627                10/10/05       0.50   
1         38.759847   -122.615627                 6/27/02       0.50   
2         38.759847   -122.615627                 2/17/06       0.50   
3         38.759847   -122.615627                 2/22/07       0.50   
4         38.759847   -122.615627                 2/22/08       0.50   
...             ...           ...                     ...        ...   
130187    39.547228   -121.131403                 5/28/02       0.02   
130188    39.054726   -121.551856                 5/23/02       0.02   
130189    39.080894   -121.333311                  5/7/02       0.02   
130190    39.343528   -121.334182                 4/26/02       0.02   
130191    39.336118   -121.268717                  5/9/02       0.02   

       GM_WELL_CATEGORY  
0             Municipal  
1             Municipal  
2             Municipal  
3             Municipal  
4    

### Convert the pd to gpd:
We need to convert the data from a pandas dataframe, to a geopandas dataframe. To do this, we have to convert the points (lat,lon) to "shapely" objects.

In [21]:
# Convert points to shapely objects, and add that as 'geometry' to the dataframe:
df['geometry'] = gpd.points_from_xy(df[lon_column_name], df[lat_column_name])

# Now just convert that Pandas dataframe to a GeoPandas dataframe:
data_gdf = gpd.GeoDataFrame(df, geometry='geometry').set_crs('EPSG:4326').to_crs(zip_gdf.crs)


In [22]:
data_gdf.head()

GM_LATITUDE  GM_LONGITUDE GM_SAMP_COLLECTION_DATE  GM_RESULT  \
0    38.759847   -122.615627                10/10/05        0.5   
1    38.759847   -122.615627                 6/27/02        0.5   
2    38.759847   -122.615627                 2/17/06        0.5   
3    38.759847   -122.615627                 2/22/07        0.5   
4    38.759847   -122.615627                 2/22/08        0.5   

  GM_WELL_CATEGORY                       geometry  
0        Municipal  POINT (-227026.156 85778.441)  
1        Municipal  POINT (-227026.156 85778.441)  
2        Municipal  POINT (-227026.156 85778.441)  
3        Municipal  POINT (-227026.156 85778.441)  
4        Municipal  POINT (-227026.156 85778.441)

### Now combine the zipcode data with the main data:
This will simply add a column with zip codes to the array. Any points that don't belong to any of the zipcodes will be removed from the dataframe 


In [23]:
filtered_gdf = data_gdf.sjoin(zip_gdf, how='inner')

# Keep only the columns we care about:
filtered_gdf = filtered_gdf[['Zipcode']+ keep_columns]

filtered_gdf.head()

Zipcode GM_SAMP_COLLECTION_DATE  GM_RESULT GM_WELL_CATEGORY
217   96088                 6/15/01       1.30        Municipal
218   96088                11/20/00       2.00        Municipal
219   96088                 11/4/96       0.77        Municipal
220   96088                10/13/99       2.00        Municipal
221   96088                10/24/02       1.50        Municipal

In [24]:
# Save file:
filtered_gdf.to_csv(f'{data_file_name[:-4]}_conc_{concentration_treshold}_zipcoded.csv', index=False)